In [0]:
# %python

from pyspark.sql.functions import *
from pyspark.sql.types import *

# Definicija šeme je i dalje ispravna i potrebna nam je
course_schema = StructType([
    StructField("id", StringType(), True), # ID je string u JSON-u, npr. "5238734"
    StructField("title", StringType(), True),
    StructField("url", StringType(), True),
    StructField("is_paid", StringType(), True), # is_paid je string "True", ne boolean
    StructField("instructor_names", StringType(), True),
    StructField("category", StringType(), True),
    StructField("headline", StringType(), True),
    StructField("num_subscribers", IntegerType(), True),
    StructField("rating", FloatType(), True),
    StructField("num_reviews", IntegerType(), True),
    StructField("instructional_level", StringType(), True),
    StructField("objectives", StringType(), True),
    StructField("curriculum", StringType(), True)
])

file_path = "/Volumes/workspace/default/project_files/udemy_courses.json" 

print(f"Čitam sirovi SSE stream sa lokacije: {file_path}")

# Korak 1: Učitaj ceo fajl kao tekstualni DataFrame, gde je svaki red jedan string
raw_text_df = spark.read.text(file_path)

# Korak 2: Filtriraj samo linije koje sadrže JSON podatke.
# One uvek počinju sa "data: ".
json_lines_df = raw_text_df.filter(col("value").startswith("data: "))

# Korak 3: Očisti "data: " prefiks da ostane samo čist JSON string.
# substring(7, ...) uzima string počevši od 7. karaktera (nakon "data: ").
clean_json_df = json_lines_df.select(
    substring(col("value"), 7, 1000000).alias("json_string")
)

# Korak 4: Sada kada imamo kolonu sa čistim JSON stringovima,
# možemo da koristimo from_json da ih parsiramo prema našoj šemi.
parsed_df = clean_json_df.select(
    from_json(col("json_string"), course_schema).alias("course_data")
)

# Korak 5: "Rasturi" strukturu da dobijemo lepe kolone.
df = parsed_df.select("course_data.*")

# Ispravka tipova podataka tamo gde je potrebno
df = df.withColumn("is_paid", col("is_paid").cast(BooleanType())) \
       .withColumn("id", col("id").cast(IntegerType()))

print("Podaci su uspešno parsirani iz SSE formata!")

df.createOrReplaceTempView("courses")
display(df)

Čitam sirovi SSE stream sa lokacije: /Volumes/workspace/default/project_files/udemy_courses.json
Podaci su uspešno parsirani iz SSE formata!


id title url is_paid instructor_names category headline num_subscribers rating num_reviews instructional_level objectives curriculum 5238734 The Complete Prompt Engineering for AI Bootcamp (2024) https://www.udemy.com/course/prompt-engineering-for-ai/ true Mike Taylor, James Phoenix Development Learn practical coding skills for working professionally with AI, including GPT-4, Stable Diffusion, and GitHub Copilot. 110503 3.9472857 43603 All Levels Learn the strengths and weaknesses of ChatGPT, Midjourney, GitHub Copilot, Stable Diffusion & other major models. Recognize the "Five Principles of Prompting", as well as common tips & tricks for professional grade output. Apply what you’ve learned to generate new AI products in 15+ real-world projects for both text and image generation use cases. Introduction, Introduction to the course, What is Prompt Engineering?, Accessing resources and prompts, Optional videos to only do if you know coding, ChatGPT AI Prompt Pack - 690 Effective Prompts, Using OpenAI Playground, Five Principles of Prompting, Give Direction, Specify Format, Provide Examples, Evaluate Quality, Divide Labor, Applying The Five Principles + Worksheet & One Pagers, How does AI work?, What are Tokens?, Log Probabilities, AI Hallucinations, Standard Text Model Practices, List Generation, Sentiment Analysis, Explain It Like I'm Five, Least to Most, Writing Clear Instructions - Detailed Instructions, Writing Clear Instructions - Specifying the Steps, Writing Clear Instructions - Delimiters, Writing Clear Instructions - Specifying Length, Let's Think Step by Step, Role Prompting, Ask for Context, Question Rewriting, Pre-Warming Chats, Progressive Summarization, Overcoming the Token Limit in ChatGPT, Advanced Text Model Techniques, Meta Prompting, Chain of Thought Reasoning, Prompt Injection, Automatic Prompt Engineer, Github Repository for the Course, Advanced List Generation - Coding, Prompt Optimization - Coding, Overcoming Token Limit - ChatGPT - Managing the Message History - Coding, Vector Databases - Coding, Reason and Act (ReAct) - Coding, Recursive Re-prompting and Revision - Coding, Information Retrieval with Vector Databases - Coding, Structured Outputs for OpenAI - Coding, What is Prompt Caching?, Prompt Caching in Practice - Coding, OpenAI Realtime - Example, AI Resource Hub, Personas of Thought, Deep Dive on LangChain - Coding, What Is LangChain? - Coding, Installation - Coding, Chat Models - Coding, Chat Prompt Templates - Coding, Streaming - Coding, Output Parsers - Coding, Summarizing Large Amounts of Text - Coding, Document Loaders, Text Splitting & Creating LangChain Documents - Coding, Tagging Documents - Coding, Tracing with LangSmith - Coding, LangChain Hub - LangSmith - Coding, LCEL - The Runnable Protocol - Coding, LCEL - Chat Models, itemgetter & RAG - Coding, LCEL - Chat Message History & Memory - Coding, LCEL - Creating Multiple Chains - Coding, LCEL - Conditional Logic, Branching & Merging - Coding, Using JSON Mode with LangChain - Coding, Exercise - Using JSON Mode with LangChain - Coding, LCEL - with JSON Mode - Coding, LCEL - with OpenAI Functions & JSON mode - Coding, Exercise - LCEL - with OpenAI Functions & JSON mode - Coding, LangChain Vector Databases + the Indexing API - Coding, LCEL Configurable Fields - Coding, LangChain Agents & Tools - Coding, Deep Dive On LangGraph - Coding, Introduction To LangGraph - Coding, Simple LangGraph Flows - Coding, Tool Usage and Persistence - Coding, Human In The Loop - Coding, Manually Updating The State - Coding, Customizing State in LangGraph - Coding, Time Travel - Coding, RAG in LangGraph (Self Corrective RAG), Extra Content To Explore In Your Own Time (Advanced Branching/Subgraphs - Coding, Proven Prompting Techniques, Chain of Thought, Emotion Prompting, Role Prompting, In Context Learning, Self-Consistency Sampling, Prompt Optimization & Evals, What are Evals?, Prompt Testing in GSheets (without code), LLM & Image Model Performance: Advanced Evalu

In [0]:
# %python

# --- Analiza 1: Top 10 najpopularnijih kategorija ---
# Cilj: Identifikovati oblasti koje privlače najviše interesovanja.
print("Analiza 1: Top 10 najpopularnijih kategorija po broju kurseva")
top_categories = spark.sql("""
  SELECT category, COUNT(*) as course_count
  FROM courses
  GROUP BY category
  ORDER BY course_count DESC
  LIMIT 10
""")
display(top_categories)

# --- Analiza 2: Korelacija između broja pretplatnika i ocene ---
# Cilj: Proveriti da li popularniji kursevi imaju tendenciju da budu bolje ocenjeni.
print("\nAnaliza 2: Korelacija između broja subscribera i ocene")
correlation = df.stat.corr("num_subscribers", "rating")
print(f"Pearson koeficijent korelacije je: {correlation}")
print("Vizuelizacija odnosa (zbog velikog broja tačaka, ovo je samo uzorak):")
display(df.select("num_subscribers", "rating").sample(0.1))

# --- Analiza 3: Analiza plaćenih vs. besplatnih kurseva ---
# Cilj: Uporediti karakteristike plaćenih i besplatnih kurseva.
print("\nAnaliza 3: Prosečan broj pretplatnika i ocena za plaćene i besplatne kurseve")
paid_vs_free = spark.sql("""
  SELECT 
    is_paid, 
    COUNT(*) as num_courses,
    ROUND(AVG(num_subscribers), 2) as avg_subscribers,
    ROUND(AVG(rating), 2) as avg_rating,
    ROUND(AVG(num_reviews), 2) as avg_reviews
  FROM courses
  GROUP BY is_paid
""")
display(paid_vs_free)

# --- Analiza 4: Koji instruktori imaju najviše visoko ocenjenih kurseva (ocena > 4.5)? ---
# Cilj: Identifikovati najuspešnije instruktore.
print("\nAnaliza 4: Top 10 instruktora sa najviše visoko ocenjenih kurseva (ocena > 4.5)")
top_instructors = spark.sql("""
  SELECT instructor_names, COUNT(*) as highly_rated_courses
  FROM courses
  WHERE rating > 4.5 AND instructor_names IS NOT NULL
  GROUP BY instructor_names
  ORDER BY highly_rated_courses DESC
  LIMIT 10
""")
display(top_instructors)

# --- Analiza 5: Popularnost kurseva po nivoima težine ---
# Cilj: Videti koji nivoi težine su najzastupljeniji i najpopularniji.
print("\nAnaliza 5: Distribucija kurseva i prosečan broj subscribera po nivou težine")
level_analysis = spark.sql("""
  SELECT 
    instructional_level,
    COUNT(*) as course_count,
    ROUND(AVG(num_subscribers)) as avg_subscribers
  FROM courses
  WHERE instructional_level IS NOT NULL
  GROUP BY instructional_level
  ORDER BY course_count DESC
""")
display(level_analysis)

Analiza 1: Top 10 najpopularnijih kategorija po broju kurseva


category course_count Development 9945 Business 9912 IT & Software 9888 Teaching & Academics 9763 Personal Development 9692 Design 9263 Health & Fitness 8559 Lifestyle 7426 Finance & Accounting 7324 Marketing 6277


Analiza 2: Korelacija između broja subscribera i ocene
Pearson koeficijent korelacije je: 0.06404517647770835
Vizuelizacija odnosa (zbog velikog broja tačaka, ovo je samo uzorak):


num_subscribers rating 2123699 4.916417 257021 4.70131 1013360 5.0 214108 3.9157357 147575 4.5550528 271973 4.1281385 70329 4.7068386 184022 5.0 99729 3.9338007 128505 4.409847 102664 4.94378 135893 5.0 75319 3.7519515 85944 4.1126704 114001 4.9551806 94593 4.486914 50345 4.6052384 110112 4.8351846 100750 4.2285275 54696 4.46547 101938 4.7335925 62577 4.137729 61452 4.323289 72753 5.0 70805 4.342172 68703 5.0 56723 4.8078732 537606 4.7778172 73721 4.4185214 378097 4.724622 38986 5.0 48493 5.0 63150 5.0 45003 5.0 39750 4.411476 90893 4.187132 35050 4.48223 30665 5.0 37027 4.803599 44895 4.6182375 44308 5.0 27471 4.223288 37091 4.566511 43513 4.936254 27508 4.1715336 26614 4.838169 22030 3.9745123 22609 4.2156367 30925 5.0 26004 4.2313843 249053 4.8457994 46710 4.617951 37192 4.8672543 20923 4.011081 38755 5.0 33256 4.289385 26586 4.116675 44263 5.0 21220 4.2073593 20984 4.5395737 25194 5.0 28560 3.7754347 42613 5.0 14313 4.190165 55464 4.089089 267195 3.8800473 27260 4.5043163 40513 4.738361 19866 4.0025454 70395 4.993144 15589 4.868145 29946 5.0 35390 4.797577 23548 4.776621 19048 4.7326393 11493 4.6651855 16116 4.678716 90013 3.7491927 14234 4.0412774 30593 5.0 296866 4.316734 25046 4.793173 32458 4.7132053 14504 5.0 13757 5.0 37975 5.0 38573 5.0 32961 3.9808855 11902 5.0 15912 4.8259525 9583 3.7846549 11251 4.0421524 26678 4.1048503 16394 4.6158648 12503 3.957118 25715 4.1312485 14220 4.202354 33501 4.855749 12118 3.8984156 24739 4.6849766 13812 5.0 12621 4.443358 11557 4.4023128 10781 4.2435756 31638 4.876212 18698 3.9108896 9940 4.212353 74032 4.0410924 16850 5.0 32628 3.5241816 12984 4.34563 18320 4.857187 6756 3.986066 12671 4.88638 8584 4.007821 9145 3.6810453 8191 4.0584693 13035 4.100967 12267 4.2611628 11164 4.1067305 23257 3.9503214 9834 4.5361667 10164 3.9937816 8838 4.214478 12832 4.4782343 11041 4.1891274 72399 5.0 15956 4.7729473 7264 4.5455127 8198 4.6837535 8614 3.8525896 11685 4.603685 8468 4.345203 18030 4.7648807 22493 4.5662813 7513 4.2688856 10410 4.0365996 106237 4.9884086 36158 4.0152454 30262 3.5764062 16770 4.181531 7851 4.0507846 7651 4.523835 8129 5.0 20432 3.3031986 4934 4.3555474 9827 4.1782637 9991 4.8325634 7560 4.793045 10284 4.0694623 11020 4.189052 62508 3.698618 5598 4.5781546 6701 4.4831257 7767 4.691893 7906 4.1787076 4813 4.3606606 7045 3.763899 7161 5.0 43295 5.0 6125 4.5682783 3570 4.5151477 8034 4.4827695 8833 4.9397807 5223 4.012988 129436 3.8638303 5531 4.483187 11447 3.6380355 97581 4.606835 11560 4.044472 7719 4.504679 8496 4.6258564 6887 4.4338827 66916 4.1045923 23011 4.465882 26300 4.804728 4906 4.1363583 6136 4.092437 39099 4.0221677 118975 4.527491 13512 4.736443 71647 3.7218711 3348 3.605215 8828 4.4729576 6065 4.5600047 4487 3.680393 14454 5.0 6388 4.6493945 6557 4.8537283 98807 3.656329 7217 4.5351624 15706 4.6769304 7904 4.935757 6806 4.4620285 34732 4.6858325 7466 4.4484243 5904 4.5366197 125960 4.575028 5442 4.0858593 62924 4.4180584 13431 5.0 5902 4.051363 5387 4.8970203 156223 4.51361 2475 4.0230527 4759 4.0706043 5066 4.9416504 4445 3.999117 5050 4.669915 3919 3.6838248 2907 2.9590466 14484 4.6584864 100276 4.2392964 5533 3.1448066 5479 4.07594 11865 4.5833983 3851 3.7635841 9995 3.8532565 13789 3.0530243 5519 4.0348096 77822 4.3666897 3101 3.972472 6349 4.488324 5429 4.6773605 67165 3.373067 5481 4.455653 8042 4.3971615 5385 4.791996 51179 3.2885559 3401 3.9199371 2003 4.5475173 8629 4.028898 4401 5.0 4739 4.3758774 3570 4.267993 31946 4.974394 5672 4.32026 68886 3.7559068 3722 4.192582 2862 4.513728 3639 4.4670453 17772 4.199497 2861 4.3682795 51857 3.6381621 5023 5.0 41442 4.292066 63089 4.3523464 4859 3.6933823 5110 4.4962444 37432 4.03359 3777 4.107423 4633 3.8608556 66987 4.4175334 1719 4.8256207 3463 4.330263 2411 4.086448 3711 5.0 2602 4.6469407 4005 3.1532664 7914 4.6261225 5301 4.6166024 2471 4.682393 5467 4.69552 4454 3.9357116 20237 4.551093 5530 4.3881207 2897 5.0 4735 4.292862 17849 4.16367 3073 4.844326 4790 5.0 5595 4.181684 26495 3.8570075 4512 4.4525


Analiza 3: Prosečan broj pretplatnika i ocena za plaćene i besplatne kurseve


is_paid num_courses avg_subscribers avg_rating avg_reviews true 93607 5662.75 4.06 542.54 false 4497 7682.29 4.17 282.9


Analiza 4: Top 10 instruktora sa najviše visoko ocenjenih kurseva (ocena > 4.5)


instructor_names highly_rated_courses Simon Sez IT 111 Infinite Skills 81 Stone River eLearning 77 Intellezy Trainers 76 Alex Genadinik 75 EDUCBA Bridging the Gap 72 Sport Videos 65 MTF Institute of Management, Technology and Finance 65 Dr. José Prabhu J 62 Eric Yeboah 62


Analiza 5: Distribucija kurseva i prosečan broj subscribera po nivou težine


instructional_level course_count avg_subscribers All Levels 53354 6539.0 Beginner Level 31551 5338.0 Intermediate Level 11455 3685.0 Expert Level 1744 2921.0

In [0]:
# %python
import os

# Putanja do fajla ostaje ista
file_path = "/Volumes/workspace/default/project_files/udemy_courses.json" 

# --- KLJUČNA IZMENA: DOBIJAMO PUTANJU DO DIREKTORIJUMA ---
# Koristimo os.path.dirname da dobijemo putanju foldera koji sadrži naš fajl
streaming_source_directory = os.path.dirname(file_path)
print(f"Streaming će pratiti direktorijum: {streaming_source_directory}")

# Putanja za checkpoint ostaje ista
checkpoint_path = "/Volumes/workspace/default/project_files/streaming_checkpoint"

# Čišćenje i parsiranje (bez promena)
# Ali sada čitamo iz direktorijuma
streaming_raw_text_df = spark.readStream.text(streaming_source_directory) 

# Sve ostalo ostaje isto...
streaming_json_lines_df = streaming_raw_text_df.filter(col("value").startswith("data: "))
streaming_clean_json_df = streaming_json_lines_df.select(
    substring(col("value"), 7, 1000000).alias("json_string")
)
streaming_parsed_df = streaming_clean_json_df.select(
    from_json(col("json_string"), course_schema).alias("course_data")
)
streaming_df = streaming_parsed_df.select("course_data.*")
streaming_df = streaming_df.withColumn("is_paid", col("is_paid").cast(BooleanType())) \
                           .withColumn("id", col("id").cast(IntegerType()))

# Streaming agregacija (bez promena)
avg_rating_per_category_stream = (streaming_df
  .groupBy("category")
  .agg(
    count("*").alias("course_count"),
    avg("rating").alias("average_rating")
  )
)
  
# WriteStream (bez promena)
streaming_query = (avg_rating_per_category_stream.writeStream
  .outputMode("complete")
  .format("memory")
  .queryName("category_ratings_stream_py")
  .trigger(availableNow=True)
  .option("checkpointLocation", checkpoint_path)
  .start()
)

streaming_query.awaitTermination()

print("Streaming query je završio sa obradom.")

Streaming će pratiti direktorijum: /Volumes/workspace/default/project_files
Streaming query je završio sa obradom.


In [0]:
# %python

# Postavite upit nad memorijskom tabelom koju je kreirao stream.
# Ovo vam omogućava da interaktivno analizirate rezultate.

streaming_results_df = spark.sql("""
  SELECT * 
  FROM category_ratings_stream_py 
  ORDER BY average_rating DESC
""")

display(streaming_results_df)

# Ako želite da vidite rezultate u konzoli umesto u Databricks tabeli:
# streaming_results_df.show()

category course_count average_rating Personal Development 9692 4.365126102289483 Teaching & Academics 9763 4.2951631526484 Business 9912 4.266771158677036 IT & Software 9888 4.248883697942719 Development 9945 4.2418722224271495 Music 3854 3.9799044989030103 Office Productivity 3955 3.922397037146215 Lifestyle 7426 3.8971756166632274 Design 9263 3.890301169618654 Photography & Video 2246 3.8145015625314636 Marketing 6277 3.778607360160482 Health & Fitness 8559 3.757501426012191 Finance & Accounting 7324 3.7358284292570687